<a href="https://colab.research.google.com/github/classic-21/Context-Driven-Question-Generation-from-PDFs/blob/main/Analytica_Hindi.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install PyPDF2 transformers pdfplumber torch

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.0/42.0 kB 1.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.5/48.5 kB 2.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.6/232.6 kB 7.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.2/59.2 kB 4.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 58.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.8/2.8 MB 75.7 MB/s eta 0:00:00


In [ ]:
import pdfplumber
from transformers import pipeline, AutoTokenizer, AutoModelForSeq2SeqLM
import textwrap
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np
import re

In [ ]:
def extract_text_from_pdf(pdf_path):
    text = ""
    with pdfplumber.open(pdf_path) as pdf:
        for page in pdf.pages:
            text += page.extract_text()
    return text

def split_text_into_paragraphs(text):
    paragraphs = text.split('\n\n')
    paragraphs = [paragraph.strip() for paragraph in paragraphs if paragraph.strip()]
    return paragraphs

def retrieve_documents(user_input, documents, top_n=10):
    vectorizer = TfidfVectorizer()
    tfidf_matrix = vectorizer.fit_transform(documents + [user_input])
    cosine_similarities = cosine_similarity(tfidf_matrix[-1], tfidf_matrix[:-1])
    related_docs_indices = np.argsort(cosine_similarities[0])[::-1][:top_n]
    return [documents[i] for i in related_docs_indices]

def generate_refined_prompt(relevant_documents, user_input):
    combined_docs = " ".join(relevant_documents)
    return combined_docs


In [ ]:
def split_text_into_chunks(text, max_chunk_size=512):
    return textwrap.wrap(text, width=max_chunk_size)

def load_model(language_code):
    '''if language_code == "en":
        model_name = "valhalla/t5-small-e2e-qg"
    elif language_code == "hi":
        model_name = "ai4bharat/indic-t5-v2-qg"
    elif language_code == "sa":
        model_name = "sanskrit-ai/sanskrit-qa"
    else:
        raise ValueError("Unsupported language code!")'''

    tokenizer = AutoTokenizer.from_pretrained("ai4bharat/MultiIndicQuestionGenerationSS", do_lower_case=False, use_fast=False, keep_accents=True)
    model = AutoModelForSeq2SeqLM.from_pretrained("ai4bharat/MultiIndicQuestionGenerationSS")

    return pipeline("text2text-generation", model=model, tokenizer=tokenizer)

def generate_questions(text, language_code="hi"):
    qg_pipeline = load_model(language_code)
    text_chunks = split_text_into_chunks(text)
    all_questions = []

    for chunk in text_chunks:
        input_text = f"generate questions: {chunk}"
        questions = qg_pipeline(input_text)
        all_questions.extend(questions)

    return all_questions

def process_pdf_for_questions(pdf_path, user_input, language_code="hi"):
    text = extract_text_from_pdf(pdf_path)
    text = split_text_into_paragraphs(text)
    relevant_documents = retrieve_documents(user_input, text)
    refined_prompt = generate_refined_prompt(relevant_documents, user_input)
    questions = generate_questions(refined_prompt, language_code)
    return questions

user_input = input("enter the topic: ")
pdf_path = "/content/godan.pdf"
language_code = "hi"
questions = process_pdf_for_questions(pdf_path, user_input, language_code)
print(questions)

for idx, q in enumerate(questions):
    print(f"Question {idx+1}: {q['generated_text']}")


enter the topic: बस सज्जन वही, जो द सरों की आबरू समझे।
<class 'str'>
["गोदान\nप्रेमचंद\n1 www.hindustanbooks.comभाग 1\nहोरीराम ने दोनों बैलों को सानी-पानी द े कर अपनी स्त्री धननया से कहा - गोबर को ऊख गोड़ने भेज दने ा। मैं न\nजाने कब लौट ूँ। जरा मेरी लाठी द े द।े धननया के दोनों हाथ गोबर से भरे थे। उपले पाथ कर आई थी। बोली -\nअरे, कुछ रस-पानी तो कर लो। ऐसी जल्दी क्या ह?ै होरी ने अपने झुर्ररयों स े भरे हुए माथे को नसकोड़ कर कहा\n- तुझे रस-पानी की पड़ी ह,ै मुझे यह चचता ह ै कक अबेर हो गई तो मानलक स े भेंट न होगी। असनान-प जा करने\nलगेंगे, तो घंटों बैठे बीत जायगा। 'इसी से तो कहती ह,ूँ कुछ जलपान कर लो और आज न जाओगे तो कौन हरज\nहोगा! अभी तो परसों गए थ।े '\n'त जो बात नहीं समझती, उसमें टाूँग क्यों अड़ाती ह ै भाई! मेरी लाठी द े द े और अपना काम दखे । यह इसी\nनमलते-जुलते रहने का परसाद ह ै कक अब तक जान बची हुई ह,ै नहीं कहीं पता न लगता कक ककधर गए। गाूँव में\nइतने आदमी तो ह,ैं ककस पर बेदखली नहीं आई, ककस पर कुड़की नहीं आई। जब दस रे के पाूँवों-तले अपनी गदनद\nदबी हुई ह,ै तो उन पाूँवों को सहलान े में ही कुस

tokenizer_config.json:   0%|          | 0.00/485 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/832 [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/1.80M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/398 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


pytorch_model.bin:   0%|          | 0.00/976M [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1258: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


[{'generated_text': 'क्या होरी का मानना था कि अगर कोई व्यक्ति उस समय के दौरान संगीत बजाना बंद'}, {'generated_text': 'किस बात पर विश्वास नहीं था कि वह एक कुशल नहीं था?'}, {'generated_text': 'स्त्री-पुरुषों में से कौन-से समूह ने चोले का नछड़ा रहता'}, {'generated_text': 'किसने उसे एक अच्छी नौकरी की तलाश में रखा?'}, {'generated_text': 'किस प्रकार के व्यक्ति का वर्णन किया जाता है?'}, {'generated_text': 'उस समय के किस भाग में एक व्यक्ति ने एक पेड़ की लकड़ी का एक टुकड़ा पकड़'}, {'generated_text': 'किस बात पर आशीवादियों का व्य ह-सा ननकल कर होरी'}, {'generated_text': 'उसने क्या कहा?'}, {'generated_text': "क्या है 'सबेरे डेस टू द ऑर डेस टू द ऑर"}, {'generated_text': 'चोपन की जीवन की सबसे बड़ी साध क्या थी?'}, {'generated_text': 'क्या है वह क्या है?'}, {'generated_text': 'उस समय की दुनिया की कौन सी स्थिति थी?'}, {'generated_text': 'किस बात पर विश्वास करनेवाले लोगों को क्या पता चला?'}, {'generated_text': '"" "हूँ" "परमेश्वर" "परमेश्वर" "पर'}, {'generated_text': 'उस समय के किस भाग पर अंग्रेजों ने कब